<a href="https://colab.research.google.com/github/tmsk0711/path-finding-rl/blob/main/Sim.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# env

In [11]:
from string import ascii_uppercase
# from draw_utils import *
# from pyglet.gl import *
import numpy as np
import pandas as pd
import os
import random



# reward!
move_reward = - 1.0
obs_reward = - 2.0
goal_reward = 10
print('reward:' , move_reward, obs_reward,goal_reward)

__file__ = '/content/drive/MyDrive/Colab Notebooks/RL/path-finding-rl/data'
local_path = os.path.abspath(os.path.join(os.path.dirname(__file__)))


class Simulator:
    def __init__(self):
        '''
        height : 그리드 높이
        width : 그리드 너비 
        inds : A ~ Q alphabet list
        '''
        # Load train data
        self.files = pd.read_csv(os.path.join(local_path, "./data/factory_order_train.csv"))
        self.height = 10
        self.width = 9
        self.inds = list(ascii_uppercase)[:17]
#        print(self.inds)
#         ['A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q']
     

    def set_box(self):
        '''
        아이템들이 있을 위치를 미리 정해놓고 그 위치 좌표들에 아이템이 들어올 수 있으므로 그리드에 100으로 표시한다.
        데이터 파일에서 이번 에피소드 아이템 정보를 받아 가져와야 할 아이템이 있는 좌표만 -100으로 표시한다.
        self.local_target에 에이전트가 이번에 방문해야할 좌표들을 저장한다.
        따라서 가져와야하는 아이템 좌표와 end point 좌표(처음 시작했던 좌표로 돌아와야하므로)가 들어가게 된다.
        '''
        box_data = pd.read_csv(os.path.join(local_path, "./data/box.csv"))
        # 아이템 위치 ex) 5,0,A | 4,0 B
        
        # 물건이 들어있을 수 있는 경우
        for box in box_data.itertuples(index = True, name ='Pandas'):
            # print(box)
            # Pandas(Index=0, row=5, col=0, item='A')
            self.grid[getattr(box, "row")][getattr(box, "col")] = 100

        # 물건이 실제 들어있는 경우
        order_item = list(set(self.inds) & set(self.items))
#         print("order_item : ",order_item)
        # [M,L,H]
        order_csv = box_data[box_data['item'].isin(order_item)]
#         print("order_csv : ",order_csv)
        # row, col, item
        
        for order_box in order_csv.itertuples(index = True, name ='Pandas'):
            self.grid[getattr(order_box, "row")][getattr(order_box, "col")] = -100
#             print("order_box : ",order_box)
#             order_box :  Pandas(Index=7, row=0, col=3, item='H')
#             order_box :  Pandas(Index=11, row=0, col=7, item='L')
#             order_box :  Pandas(Index=12, row=0, col=8, item='M')
            # local target에 가야 할 위치 좌표 넣기
            self.local_target.append(
                [getattr(order_box, "row"),
                 getattr(order_box, "col")]
                )

        self.local_target.sort()
        self.local_target.append([9,4]) 
#         print(self.local_target)
        # 알파벳을 Grid에 넣어서 -> grid에 2Dconv 적용 가능

    def set_obstacle(self):
        '''
        장애물이 있어야하는 위치는 미리 obstacles.csv에 정의되어 있다. 이 좌표들을 0으로 표시한다.
        '''
        obstacles_data = pd.read_csv(os.path.join(local_path, "./data/obstacles.csv"))
        
        for obstacle in obstacles_data.itertuples(index = True, name ='Pandas'):
            self.grid[getattr(obstacle, "row")][getattr(obstacle, "col")] = 0
#             print("self.grid:\n ",self.grid)

    def reset(self, epi):
        '''
        reset()은 첫 스텝에서 사용되며 그리드에서 에이전트 위치가 start point에 있게 한다.

        :param epi: episode, 에피소드 마다 가져와야 할 아이템 리스트를 불러올 때 사용
        :return: 초기셋팅 된 그리드
        :rtype: numpy.ndarray
        _____________________________________________________________________________________
        items : 이번 에피소드에서 가져와야하는 아이템들
        terminal_location : 현재 에이전트가 찾아가야하는 목적지
        local_target : 한 에피소드에서 찾아가야하는 아이템 좌표, 마지막 엔드 포인트 등의 위치좌표들
        actions: visualization을 위해 에이전트 action을 저장하는 리스트
        curloc : 현재 위치
        '''

        # initial episode parameter setting
        self.epi = epi
        self.items = list(self.files.iloc[self.epi])[0]
        self.cumulative_reward = 0
        self.terminal_location = None
        self.local_target = []
        self.actions = []

        # initial grid setting
        self.grid = np.ones((self.height, self.width), dtype="float16")

        # set information about the gridworld
        self.set_box()
        self.set_obstacle()

        # start point를 grid에 표시
        self.curloc = [9, 4]
        self.grid[int(self.curloc[0])][int(self.curloc[1])] = -5
        
        self.done = False
        
        return self.grid

    def apply_action(self, action, cur_x, cur_y):
        '''
        에이전트가 행한 action대로 현 에이전트의 위치좌표를 바꾼다.
        action은 discrete하며 4가지 up,down,left,right으로 정의된다.
        
        :param x: 에이전트의 현재 x 좌표
        :param y: 에이전트의 현재 y 좌표
        :return: action에 따라 변한 에이전트의 x 좌표, y 좌표
        :rtype: int, int
        '''
        new_x = cur_x
        new_y = cur_y
        # up
        if action == 0:
            new_x = cur_x - 1
        # down
        elif action == 1:
            new_x = cur_x + 1
        # left
        elif action == 2:
            new_y = cur_y - 1
        # right
        else:
            new_y = cur_y + 1

        return int(new_x), int(new_y)


    def get_reward(self, new_x, new_y, out_of_boundary):
        '''
        get_reward함수는 리워드를 계산하는 함수이며, 상황에 따라 에이전트가 action을 옳게 했는지 판단하는 지표가 된다.

        :param new_x: action에 따른 에이전트 새로운 위치좌표 x
        :param new_y: action에 따른 에이전트 새로운 위치좌표 y
        :param out_of_boundary: 에이전트 위치가 그리드 밖이 되지 않도록 제한
        :return: action에 따른 리워드
        :rtype: float
        '''

        # 바깥으로 나가는 경우
        if any(out_of_boundary):
            reward = obs_reward
            print( '나감')
                       
        else:
            # 장애물에 부딪히는 경우 
            if self.grid[new_x][new_y] == 0:
                reward = obs_reward  
                print('부딪힘')

            # 현재 목표에 도달한 경우
            elif new_x == self.terminal_location[0] and new_y == self.terminal_location[1]:
                reward = goal_reward
                print('목표 도달')

            # 그냥 움직이는 경우 
            else:
                reward = move_reward
                print('이동')

        return reward

    def step(self, action):
        ''' 
        에이전트의 action에 따라 step을 진행한다.
        action에 따라 에이전트 위치를 변환하고, action에 대해 리워드를 받고, 어느 상황에 에피소드가 종료되어야 하는지 등을 판단한다.
        에이전트가 endpoint에 도착하면 gif로 에피소드에서 에이전트의 행동이 저장된다.

        :param action: 에이전트 행동
        :return:
            grid, 그리드
            reward, 리워드
            cumulative_reward, 누적 리워드
            done, 종료 여부
            goal_ob_reward, goal까지 아이템을 모두 가지고 돌아오는 finish율 계산을 위한 파라미터

        :rtype: numpy.ndarray, float, float, bool, bool/str

        (Hint : 시작 위치 (9,4)에서 up말고 다른 action은 전부 장애물이므로 action을 고정하는 것이 좋음)
        '''

        #==============================수정
#         print("local_target",self.local_target)
        
#         local_target_len = len(self.local_target)
        
#         for i in range(local_target_len):
            
#             self.terminal_location = self.local_target[i]
        
        
            #==============================수정
        self.terminal_location = self.local_target[0]
        
        cur_x,cur_y = self.curloc
        self.actions.append((cur_x, cur_y))

        goal_ob_reward = False
        
        new_x, new_y = self.apply_action(action, cur_x, cur_y)

        out_of_boundary = [new_x < 0, new_x >= self.height, new_y < 0, new_y >= self.width]

        # 바깥으로 나가는 경우 종료
        if any(out_of_boundary):
            self.done = True
            goal_ob_reward = True
        else:
            # 장애물에 부딪히는 경우 종료
            if self.grid[new_x][new_y] == 0:
                self.done = True
                goal_ob_reward = True

            # 현재 목표에 도달한 경우, 다음 목표설정
            elif new_x == self.terminal_location[0] and new_y == self.terminal_location[1]:

                # end point 일 때
                if [new_x, new_y] == [9,4]:
                    self.done = True

                self.local_target.remove(self.local_target[0])
                self.grid[cur_x][cur_y] = 1
                self.grid[new_x][new_y] = -5
                goal_ob_reward = True
                self.curloc = [new_x, new_y]
            else:
                # 그냥 움직이는 경우 
                self.grid[cur_x][cur_y] = 1
                self.grid[new_x][new_y] = -5
                self.curloc = [new_x,new_y]
                
        reward = self.get_reward(new_x, new_y, out_of_boundary)
        self.cumulative_reward += reward

        # if self.done == True:
        #     if [new_x, new_y] == [9, 4]:
        #         if self.terminal_location == [9, 4]:
        #             # 완료되면 GIFS 저장
        #             goal_ob_reward = 'finish'
        #             height = 10
        #             width = 9 
        #             display = Display(visible=False, size=(width, height))
        #             display.start()

        #             start_point = (9, 4)
        #             unit = 50
        #             screen_height = height * unit
        #             screen_width = width * unit
        #             log_path = "./logs"
        #             data_path = "./data"
        #             render_cls = Render(screen_width, screen_height, unit, start_point, data_path, log_path)
        #             for idx, new_pos in enumerate(self.actions):
        #                 render_cls.update_movement(new_pos, idx+1)
                    
        #             render_cls.save_gif(self.epi)
        #             render_cls.viewer.close()
        #             display.stop()
        # else:
        #     if [new_x, new_y] == [9, 4]:
        #         if self.terminal_location == [9, 4]:
        #             # 완료되면 GIFS 저장
        #             goal_ob_reward = 'finish'
        #             height = 10
        #             width = 9 
        #             display = Display(visible=False, size=(width, height))
        #             display.start()

        #             start_point = (9, 4)
        #             unit = 50
        #             screen_height = height * unit
        #             screen_width = width * unit
        #             log_path = "./logs"
        #             data_path = "./data"
        #             render_cls = Render(screen_width, screen_height, unit, start_point, data_path, log_path)
        #             for idx, new_pos in enumerate(self.actions):
        #                 render_cls.update_movement(new_pos, idx+1)
                    
        #             render_cls.save_gif(self.epi)
        #             render_cls.viewer.close()
        #             display.stop()           
        
        # return int(new_x), int(new_y), self.grid, reward, self.cumulative_reward, self.done, goal_ob_reward        


    


reward: -1.0 -2.0 10


# Policy

In [56]:
import collections
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim

class Policy():
    def __init__(self):
        pass
    
class RandomPolicy(Policy):
    def __init__(self):
        pass
    
    def select_action(self):
        action = random.randint(0,3)
        return action

class MC_Policy(Policy):
    def __init__(self):
        self.q_table = np.zeros((5,7,4))
        self.eps = 0.9
        self.alpha = 0.01
    def select_action(self,s):
        coin = random.randint(0,3)



# DQN
gamma = 0.98
buffer_limit = 50000
batch_size = 32
learning_rate = 0.0005

    # 리플레이 버퍼 추가
class ReplayBuffer():

    def __init__(self):   
        self.buffer = collections.deque(maxlen=buffer_limit)
    
    def put(self, transition):
        self.buffer.append(transition)
    
    def sample(self, n):
        mini_batch = random.sample(self.buffer, n)
        s_lst, a_lst, r_lst, s_prime_lst, done_mask_lst = [], [], [], [], []
        
        for transition in mini_batch:
            s, a, r, s_prime, done_mask = transition
            s_lst.append(s)
            a_lst.append([a])
            r_lst.append([r])
            s_prime_lst.append(s_prime)
            done_mask_lst.append([done_mask])

        return torch.tensor(s_lst, dtype=torch.float), torch.tensor(a_lst), \
               torch.tensor(r_lst), torch.tensor(s_prime_lst, dtype=torch.float), \
               torch.tensor(done_mask_lst)
    
    def size(self):
        return len(self.buffer)

      
class Qnet(nn.Module):
    def __init__(self):
        super(Qnet, self).__init__()
        self.fc1 = nn.Linear(4, 128)
        self.fc2 = nn.Linear(128, 128)
        self.fc3 = nn.Linear(128, 2)

    def forward(self, x):
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x
      
    def sample_action(self, obs, epsilon):
        out = self.forward(obs)
        coin = random.random()
        if coin < epsilon:
            return random.randint(0,1)
        else : 
            return out.argmax().item()
            
    def train(q, q_target, memory, optimizer):
        for i in range(10):
            s,a,r,s_prime,done_mask = memory.sample(batch_size)

            q_out = q(s)
            q_a = q_out.gather(1,a)
            max_q_prime = q_target(s_prime).max(1)[0].unsqueeze(1)
            target = r + gamma * max_q_prime * done_mask
            loss = F.smooth_l1_loss(q_a, target)
            
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()       

In [58]:
def main():
    sim = Simulator() 
    q = Qnet()
    files = pd.read_csv("/content/drive/MyDrive/Colab Notebooks/RL/path-finding-rl/data/factory_order_train.csv")
    q_target = Qnet()
    q_target.load_state_dict(q.state_dict())
    memory = ReplayBuffer()

    print_interval = 20
    score = 0.0  
    optimizer = optim.Adam(q.parameters(), lr=learning_rate)

    for n_epi in range(10):
        epsilon = max(0.01, 0.08 - 0.01*(n_epi/200)) #Linear annealing from 8% to 1%
        s = sim.reset()
        done = False

        while not done:
            a = q.sample_action(torch.from_numpy(s).float(), epsilon)      
            s_prime, r, done, info = sim.step(a)
            done_mask = 0.0 if done else 1.0
            memory.put((s,a,r/100.0,s_prime, done_mask))
            s = s_prime

            score += r
            if done:
                break
            
        if memory.size()>2000:
            train(q, q_target, memory, optimizer)

        if n_epi%print_interval==0 and n_epi!=0:
            q_target.load_state_dict(q.state_dict())
            print("n_episode :{}, score : {:.1f}, n_buffer : {}, eps : {:.1f}%".format(
                                                            n_epi, score/print_interval, memory.size(), epsilon*100))
            score = 0.0
    sim.close()

if __name__ == '__main__':
    main()

TypeError: ignored

# Agent

In [50]:
"========================================================agent"
class Agent():
    def __init__(self):
        self.target_list = None
        self.policy = None
        
    def set_target_list(self, local_target):
        self.target_list = local_target
        print("Agent's local target = {}".format(local_target))
    
    def select_action(self):
        action = self.policy.select_action()
        return action
    
    def set_policy(self, mode):
        if mode=='random':
            self.policy = RandomPolicy()
            print(r"Agent's Policy = random")
            
        if mode == 'MC' :
            self.policy = MC_Policy()
            print(r"Agent's Policy = MC")
            
        if mode == 'DQN' :
            self.policy = DQN()
            print(r"Agent's Policy = DQN")

#  RandomTD_Main

In [ ]:
if __name__ == "__main__":
    
    sim = Simulator()
    files = pd.read_csv("./data/factory_order_train.csv")
    agent = Agent()
    agent.set_policy('random')
    data = np.zeros((10,9))
    gamma = 1.0
    alpha = 0.0001
    
    for epi in range(10000): # len(files)):
        # env 초기화
        obs = sim.reset(epi)
        print('\n\nenv 초기화 완료, {}번째 에피소드 시작'.format(epi))
        
        history = []
        
#         print("data:",data)
        items = list(files.iloc[epi])[0]
        print("itmes",items)
        agent.set_target_list(items)
        done = False

#         actions = [0, 0, 2, 2, 2, 0, 0, 0, 0, 0, 0, 0, 3, 3, 3, 3, 3, 3, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 1]
        
        while done == False:
            actions = agent.select_action()
            print("action :",actions)
    
            
            x, y, next_obs, reward, cumul ,done, goal_reward = sim.step(actions)
            obs = next_obs
            
            # =============== history 추가 
            history.append((x,y,reward))
            print(history)
            
        cum_reward = 0
        for transition in history[::-1]:
            x,y,reward = transition

            print("data: ",data[x][y])
            data[x][y] = data[x][y] + alpha*(cum_reward - data[x][y])                
            cum_reward = cum_reward + gamma * reward
            
    for row in data:
        print("row\n",row)
            
            
            
#             print((x,y))
#             print("next_obs: \n ",next_obs)
#             print("reward: ",reward)
#             print("cumul: ",cumul)
#             print("done: ",done)
#             print("goal_reward: ",goal_reward)
            
#             print(i)
#             if (done == True) or (i == (len(actions)-1)):
#                 i =0
                



       
#         while done == False:
# #             actions = agent.select_action()
# #             print('actions:',actions)
#             i += 1
#             next_obs, reward, cumul ,done, goal_reward = sim.step(actions[i])
# #             print(actions[i])    
#             print("next_obs: ",next_obs)
#             print("reward: ",reward)
#             print("cumul: ",cumul)
#             print("done: ",done)
#             print("goal_reward: ",goal_reward)
#             obs = next_obs

#             if (done == True) or (i == (len(actions)-1)):
#                 i =0


            


Agent's Policy = random


env 초기화 완료, 0번째 에피소드 시작
itmes ['H', 'L', 'M']
Agent's local target = ['H', 'L', 'M']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 1번째 에피소드 시작
itmes ['F', 'M', 'O', 'P', 'Q']
Agent's local target = ['F', 'M', 'O', 'P', 'Q']
action : 0
이동
[(8, 4, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (8, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (8, 4, 0.1)]
action : 3
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (8, 4, 0.1), (8, 5, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (8, 4, 0.1), (8, 5, 0.1), (7, 5, 0.1)]
action : 0
이동
[(8, 4, 



env 초기화 완료, 34번째 에피소드 시작
itmes ['A', 'D', 'K', 'L', 'M', 'P']
Agent's local target = ['A', 'D', 'K', 'L', 'M', 'P']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 35번째 에피소드 시작
itmes ['B', 'D', 'J', 'L', 'N', 'O', 'P']
Agent's local target = ['B', 'D', 'J', 'L', 'N', 'O', 'P']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 36번째 에피소드 시작
itmes ['D', 'G', 'J']
Agent's local target = ['D', 'G', 'J']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 37번째 에피소드 시작
itmes ['C', 'E', 'G', 'M', 'P', 'Q']
Agent's local target = ['C', 'E', 'G', 'M', 'P', 'Q']
action : 0
이동
[(8, 4, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1)]
action : 0
부딪힘
[(8, 4, 0.1), (7, 4, 0.1), (6, 4, 0.1)]
data:  0.0
data:  0.00021994400699957003
data:  0.0008094622294346232


env 초기화 완료, 38번째 에피소드 시작
itmes ['D', 'E', 'F', 'L', 'M', 'P', 'Q']
Agent's local target = ['D', 'E', 'F', 'L', 'M', 'P', 'Q']
action : 1
나감
[(10, 4, 0.1)]
data:  0.0


env 초기화 완료, 39번째 에피소드 시작
itmes ['F', 'G', 'H', 'L', 'O']
Agent's



env 초기화 완료, 71번째 에피소드 시작
itmes ['E', 'G', 'H', 'I', 'L', 'M']
Agent's local target = ['E', 'G', 'H', 'I', 'L', 'M']
action : 2
부딪힘
[(9, 3, 0.1)]
data:  0.0


env 초기화 완료, 72번째 에피소드 시작
itmes ['C']
Agent's local target = ['C']
action : 0
이동
[(8, 4, 0.1)]
action : 3
이동
[(8, 4, 0.1), (8, 5, 0.1)]
action : 2
이동
[(8, 4, 0.1), (8, 5, 0.1), (8, 4, 0.1)]
action : 2
이동
[(8, 4, 0.1), (8, 5, 0.1), (8, 4, 0.1), (8, 3, 0.1)]
action : 2
이동
[(8, 4, 0.1), (8, 5, 0.1), (8, 4, 0.1), (8, 3, 0.1), (8, 2, 0.1)]
action : 2
이동
[(8, 4, 0.1), (8, 5, 0.1), (8, 4, 0.1), (8, 3, 0.1), (8, 2, 0.1), (8, 1, 0.1)]
action : 2
이동
[(8, 4, 0.1), (8, 5, 0.1), (8, 4, 0.1), (8, 3, 0.1), (8, 2, 0.1), (8, 1, 0.1), (8, 0, 0.1)]
action : 0
이동
[(8, 4, 0.1), (8, 5, 0.1), (8, 4, 0.1), (8, 3, 0.1), (8, 2, 0.1), (8, 1, 0.1), (8, 0, 0.1), (7, 0, 0.1)]
action : 1
이동
[(8, 4, 0.1), (8, 5, 0.1), (8, 4, 0.1), (8, 3, 0.1), (8, 2, 0.1), (8, 1, 0.1), (8, 0, 0.1), (7, 0, 0.1), (8, 0, 0.1)]
action : 1
부딪힘
[(8, 4, 0.1), (8, 5, 0.1), (8, 4, 0.1),



env 초기화 완료, 104번째 에피소드 시작
itmes ['K', 'L', 'M', 'N']
Agent's local target = ['K', 'L', 'M', 'N']
action : 1
나감
[(10, 4, 0.1)]
data:  0.0


env 초기화 완료, 105번째 에피소드 시작
itmes ['E', 'I']
Agent's local target = ['E', 'I']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 106번째 에피소드 시작
itmes ['C', 'D', 'G', 'J', 'P']
Agent's local target = ['C', 'D', 'G', 'J', 'P']
action : 2
부딪힘
[(9, 3, 0.1)]
data:  0.0


env 초기화 완료, 107번째 에피소드 시작
itmes ['I', 'M']
Agent's local target = ['I', 'M']
action : 2
부딪힘
[(9, 3, 0.1)]
data:  0.0


env 초기화 완료, 108번째 에피소드 시작
itmes ['C', 'E', 'H', 'K', 'M', 'Q']
Agent's local target = ['C', 'E', 'H', 'K', 'M', 'Q']
action : 2
부딪힘
[(9, 3, 0.1)]
data:  0.0


env 초기화 완료, 109번째 에피소드 시작
itmes ['E', 'F', 'G', 'J']
Agent's local target = ['E', 'F', 'G', 'J']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 110번째 에피소드 시작
itmes ['A', 'B', 'F', 'I', 'J', 'L', 'M']
Agent's local target = ['A', 'B', 'F', 'I', 'J', 'L', 'M']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초

data:  0.00021997800119997004
data:  0.0003299320132981702
data:  0.0005697620801810633
data:  0.0008093453806355937
data:  0.0029913408430798497


env 초기화 완료, 177번째 에피소드 시작
itmes ['D', 'G', 'H', 'J', 'K', 'N', 'Q']
Agent's local target = ['D', 'G', 'H', 'J', 'K', 'N', 'Q']
action : 2
부딪힘
[(9, 3, 0.1)]
data:  0.0


env 초기화 완료, 178번째 에피소드 시작
itmes ['C', 'E', 'I', 'J', 'K', 'P', 'Q']
Agent's local target = ['C', 'E', 'I', 'J', 'K', 'P', 'Q']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 179번째 에피소드 시작
itmes ['C', 'L']
Agent's local target = ['C', 'L']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 180번째 에피소드 시작
itmes ['I', 'O', 'Q']
Agent's local target = ['I', 'O', 'Q']
action : 2
부딪힘
[(9, 3, 0.1)]
data:  0.0


env 초기화 완료, 181번째 에피소드 시작
itmes ['J']
Agent's local target = ['J']
action : 0
이동
[(8, 4, 0.1)]
action : 2
이동
[(8, 4, 0.1), (8, 3, 0.1)]
action : 3
이동
[(8, 4, 0.1), (8, 3, 0.1), (8, 4, 0.1)]
action : 0
이동
[(8, 4, 0.1), (8, 3, 0.1), (8, 4, 0.1), (7, 4, 0.1)]
action : 

...



env 초기화 완료, 9844번째 에피소드 시작
itmes ['A', 'D', 'E', 'F', 'P', 'Q']
Agent's local target = ['A', 'D', 'E', 'F', 'P', 'Q']
action : 1
나감
[(10, 4, 0.1)]
data:  0.0


env 초기화 완료, 9845번째 에피소드 시작
itmes ['B', 'C', 'D', 'O', 'Q']
Agent's local target = ['B', 'C', 'D', 'O', 'Q']
action : 0
이동
[(8, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (9, 4, 0.1)]
action : 3
부딪힘
[(8, 4, 0.1), (9, 4, 0.1), (9, 5, 0.1)]
data:  0.0
data:  0.020540632739751354
data:  0.16009088996436313


env 초기화 완료, 9846번째 에피소드 시작
itmes ['A', 'B', 'G', 'H', 'K', 'O', 'Q']
Agent's local target = ['A', 'B', 'G', 'H', 'K', 'O', 'Q']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기화 완료, 9847번째 에피소드 시작
itmes ['C', 'F', 'I', 'J', 'K', 'N', 'Q']
Agent's local target = ['C', 'F', 'I', 'J', 'K', 'N', 'Q']
action : 0
이동
[(8, 4, 0.1)]
action : 2
이동
[(8, 4, 0.1), (8, 3, 0.1)]
action : 3
이동
[(8, 4, 0.1), (8, 3, 0.1), (8, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (8, 3, 0.1), (8, 4, 0.1), (9, 4, 0.1)]
action : 2
부딪힘
[(8, 4, 0.1), (8, 3, 0.1), (8, 4, 0

action : 3
이동
[(8, 4, 0.1), (8, 5, 0.1)]
action : 1
부딪힘
[(8, 4, 0.1), (8, 5, 0.1), (9, 5, 0.1)]
data:  0.0
data:  0.0551166230725783
data:  0.16055467206477161


env 초기화 완료, 9879번째 에피소드 시작
itmes ['B', 'F', 'G', 'H', 'N', 'P', 'Q']
Agent's local target = ['B', 'F', 'G', 'H', 'N', 'P', 'Q']
action : 0
이동
[(8, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (9, 4, 0.1)]
action : 1
나감
[(8, 4, 0.1), (9, 4, 0.1), (10, 4, 0.1)]
data:  0.0
data:  0.02056446816622787
data:  0.16055861659756512


env 초기화 완료, 9880번째 에피소드 시작
itmes ['B', 'C', 'F', 'K', 'Q']
Agent's local target = ['B', 'C', 'F', 'K', 'Q']
action : 1
나감
[(10, 4, 0.1)]
data:  0.0


env 초기화 완료, 9881번째 에피소드 시작
itmes ['A', 'D', 'F', 'H', 'I', 'K', 'M']
Agent's local target = ['A', 'D', 'F', 'H', 'I', 'K', 'M']
action : 1
나감
[(10, 4, 0.1)]
data:  0.0


env 초기화 완료, 9882번째 에피소드 시작
itmes ['B', 'C', 'D', 'E', 'I', 'J']
Agent's local target = ['B', 'C', 'D', 'E', 'I', 'J']
action : 1
나감
[(10, 4, 0.1)]
data:  0.0


env 초기화 완료, 9883번째 에피소드 시작
itmes ['D', 



env 초기화 완료, 9913번째 에피소드 시작
itmes ['B', 'D', 'F', 'I', 'J', 'K', 'M']
Agent's local target = ['B', 'D', 'F', 'I', 'J', 'K', 'M']
action : 2
부딪힘
[(9, 3, 0.1)]
data:  0.0


env 초기화 완료, 9914번째 에피소드 시작
itmes ['B', 'G', 'I', 'N', 'P', 'Q']
Agent's local target = ['B', 'G', 'I', 'N', 'P', 'Q']
action : 0
이동
[(8, 4, 0.1)]
action : 2
이동
[(8, 4, 0.1), (8, 3, 0.1)]
action : 3
이동
[(8, 4, 0.1), (8, 3, 0.1), (8, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (8, 3, 0.1), (8, 4, 0.1), (9, 4, 0.1)]
action : 3
부딪힘
[(8, 4, 0.1), (8, 3, 0.1), (8, 4, 0.1), (9, 4, 0.1), (9, 5, 0.1)]
data:  0.0
data:  0.020596237613147203
data:  0.16116573228799894
data:  0.054456603655789707
data:  0.16116961571477015


env 초기화 완료, 9915번째 에피소드 시작
itmes ['C', 'F', 'G', 'H', 'J', 'K']
Agent's local target = ['C', 'F', 'G', 'H', 'J', 'K']
action : 2
부딪힘
[(9, 3, 0.1)]
data:  0.0


env 초기화 완료, 9916번째 에피소드 시작
itmes ['A', 'C', 'F', 'G', 'N']
Agent's local target = ['A', 'C', 'F', 'G', 'N']
action : 3
부딪힘
[(9, 5, 0.1)]
data:  0.0


env 초기



env 초기화 완료, 9947번째 에피소드 시작
itmes ['B', 'D', 'F', 'I', 'L', 'M', 'O']
Agent's local target = ['B', 'D', 'F', 'I', 'L', 'M', 'O']
action : 0
이동
[(8, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (9, 4, 0.1)]
action : 1
나감
[(8, 4, 0.1), (9, 4, 0.1), (10, 4, 0.1)]
data:  0.0
data:  0.020627994354193806
data:  0.16137608259539027


env 초기화 완료, 9948번째 에피소드 시작
itmes ['F', 'G', 'H', 'I', 'L', 'P', 'Q']
Agent's local target = ['F', 'G', 'H', 'I', 'L', 'P', 'Q']
action : 0
이동
[(8, 4, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1)]
action : 1
이동
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1)]
action : 3
부딪힘
[(8, 4, 0.1), (7, 4, 0.1), (8, 4, 0.1), (9, 4, 0.1), (9, 5, 0.1)]
data:  0.0
data:  0.020635931554758388
data:  0.16137994498713074
data:  0.06480973592299498
data:  0.16138380699263202


env 초기화 완료, 9949번째 에피소드 시작
itmes ['C', 'E', 'G', 'K', 'L', 'O', 'P']
Agent's local target = ['C', 'E', 'G', 'K', 'L', 'O', 'P']
action : 3
부딪힘
[(9, 5, 0.1)]




env 초기화 완료, 9982번째 에피소드 시작
itmes ['C', 'G', 'I', 'K', 'L', 'M', 'O']
Agent's local target = ['C', 'G', 'I', 'K', 'L', 'M', 'O']
action : 0
이동
[(8, 4, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1)]
action : 3
이동
[(8, 4, 0.1), (7, 4, 0.1), (7, 5, 0.1)]
action : 2
이동
[(8, 4, 0.1), (7, 4, 0.1), (7, 5, 0.1), (7, 4, 0.1)]
action : 2
이동
[(8, 4, 0.1), (7, 4, 0.1), (7, 5, 0.1), (7, 4, 0.1), (7, 3, 0.1)]
action : 1
이동
[(8, 4, 0.1), (7, 4, 0.1), (7, 5, 0.1), (7, 4, 0.1), (7, 3, 0.1), (8, 3, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1), (7, 5, 0.1), (7, 4, 0.1), (7, 3, 0.1), (8, 3, 0.1), (7, 3, 0.1)]
action : 0
이동
[(8, 4, 0.1), (7, 4, 0.1), (7, 5, 0.1), (7, 4, 0.1), (7, 3, 0.1), (8, 3, 0.1), (7, 3, 0.1), (6, 3, 0.1)]
action : 1
이동
[(8, 4, 0.1), (7, 4, 0.1), (7, 5, 0.1), (7, 4, 0.1), (7, 3, 0.1), (8, 3, 0.1), (7, 3, 0.1), (6, 3, 0.1), (7, 3, 0.1)]
action : 3
이동
[(8, 4, 0.1), (7, 4, 0.1), (7, 5, 0.1), (7, 4, 0.1), (7, 3, 0.1), (8, 3, 0.1), (7, 3, 0.1), (6, 3, 0.1), (7, 3, 0.1), (7, 4, 0.1)]
actio

In [10]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# 몬테카를로 prediction 4방향 랜덤 정책 구현
* 값이 정확하게 나오지 않을 뿐더러 이 방법은 매번 골 포인트가 달라지니 엄청나게 많은 계산을 해야되고 매번 골 포인트가 바뀔때마다 다시 계산을 해야되서 좋지 않은 방법이라 생각을 했다.
